### Загрузка всех бассейнов из JSON

Предобработка и создание единого хранилища с нуными metadata. Хранится в `processed_output/all_documents`

In [1]:
# импорт библиотек
import os
import json
import pandas as pd
import re

from transformers import AutoTokenizer
from langchain_core.documents import Document

/Users/anastasia/docs/Projects/skiovo_project/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
root_folder = "../../data/JSON"

# Получаем все пути к папкам, содержащим название "Исходные"
result_paths = []
for dirpath, dirnames, filenames in os.walk(root_folder):
    for dirname in dirnames:
        if "Исходные" in dirname:
            result_paths.append(os.path.join(dirpath, dirname))

result_paths

['../../data/JSON/Печора/Исходные',
 '../../data/JSON/Обь/Исходные',
 '../../data/JSON/Дон/Исходные',
 '../../data/JSON/Терек/Исходные',
 '../../data/JSON/Кубань/Исходные',
 '../../data/JSON/Сура/Исходные',
 '../../data/JSON/Волга/Исходные',
 '../../data/JSON/Урал/Исходные']

In [17]:
# Функция для получения списка всех JSON-файлов в папках
def get_all_json_files_from_paths(paths):
    json_files = []
    for path in paths:
        for root, _, files in os.walk(path):
            for file in files:
                if file.endswith(".json"):
                    json_files.append(os.path.join(root, file))
    return json_files

# Чтение и обработка JSON-файлов
def process_json_file(file_path, basin_name):
    """
    Обрабатывает один JSON-файл и возвращает список документов.
    """
    with open(file_path, "r", encoding="utf-8") as file:
        data = json.load(file)
    
    def extract_documents_recursive(sections, parent_title="", parent_level=0):
        documents = []
        for section in sections:
            title = section.get("title", "No Title")
            level = section.get("level", parent_level + 1)
            start_page = section.get("start_page", 0)
            end_page = section.get("end_page", 0)
            text = section.get("text", "")

            metadata = {
                "title": title,
                "level": level,
                "parent_title": parent_title,
                "start_page": start_page,
                "end_page": end_page,
                "file": os.path.basename(file_path),
                "basin": basin_name  # Добавляем название бассейна
            }

            documents.append(Document(page_content=text, metadata=metadata))

            if "subsections" in section and isinstance(section["subsections"], list):
                documents.extend(
                    extract_documents_recursive(
                        section["subsections"], parent_title=title, parent_level=level
                    )
                )
        return documents

    documents = extract_documents_recursive(data)

    def remove_table_and_save_titles(text):
        table_pattern = re.compile(
            r'((?:Таблица\s[\d.]+|Продолжение таблицы.*?)\s.*?)(?:\n.*?)+(?=(?:\n[А-Яа-я]|$))',
            re.DOTALL
        )
        figure_pattern = re.compile(r'(?:рис\.|Рис\.|Рисунок)\s[\d.]+\s-.*?(?=\n|$)', re.IGNORECASE)
        cleaned_text = table_pattern.sub(r'\1', text)
        figures = figure_pattern.findall(text)
        for figure in figures:
            if figure not in cleaned_text:
                cleaned_text += f"\n{figure}\n"
        return cleaned_text

    for doc in documents:
        doc.page_content = remove_table_and_save_titles(doc.page_content)

    def preprocess_page_content(text):
        text = re.sub(r"\s+", " ", text)
        text = re.sub(r"\b([А-ЯЁ]{2,})\b", lambda m: m.group(1).capitalize(), text)
        text = re.sub(r"[^\w\s.,!?-–—()\"']", " ", text)
        return text.strip()

    for doc in documents:
        doc.page_content = preprocess_page_content(doc.page_content)

    return documents

# Обработка всех JSON-файлов из всех папок
all_documents = []
for path in result_paths:
    basin_name = os.path.basename(os.path.dirname(path))  # Название бассейна (например, "Печора")
    json_files = get_all_json_files_from_paths([path])
    for json_file in json_files:
        all_documents.extend(process_json_file(json_file, basin_name))

# Постобработка: разбиение на части и добавление метаданных
model_name = "deepvk/USER-bge-m3"
tokenizer = AutoTokenizer.from_pretrained(model_name)

def split_text_with_overlap(text, max_tokens, overlap=100):
    tokens = tokenizer(text, add_special_tokens=False)["input_ids"]
    num_tokens = len(tokens)
    if num_tokens <= max_tokens:
        return [text]
    
    chunks = []
    start = 0
    while start < num_tokens:
        end = min(start + max_tokens, num_tokens)
        chunk_tokens = tokens[start:end]
        chunk_text = tokenizer.decode(chunk_tokens, skip_special_tokens=True)
        chunks.append(chunk_text)
        start += max_tokens - overlap
    return chunks

def process_documents_with_overlap(documents, max_tokens=1024, overlap=100):
    processed_documents = []
    for doc in documents:
        chunks = split_text_with_overlap(doc.page_content, max_tokens, overlap)
        for idx, chunk in enumerate(chunks):
            new_metadata = doc.metadata.copy()
            new_metadata["chunk_index"] = idx + 1
            new_metadata["total_chunks"] = len(chunks)
            processed_documents.append(Document(metadata=new_metadata, page_content=chunk))
    return processed_documents

processed_documents = process_documents_with_overlap(all_documents)

for idx, doc in enumerate(processed_documents, start=1):
    doc.metadata["order"] = idx

processed_documents = sorted(processed_documents, key=lambda x: x.metadata["order"])

# Вывод количества обработанных документов
print(f"Обработано бассейнов: {len(result_paths)}")
print(f"Обработано документов: {len(processed_documents)}")

Token indices sequence length is longer than the specified maximum sequence length for this model (8848 > 8192). Running this sequence through the model will result in indexing errors


Обработано бассейнов: 8
Обработано документов: 2328


In [19]:
print(2328 * 2)

4656


In [18]:
processed_documents

[Document(metadata={'title': 'ВВЕДЕНИЕ', 'level': 1, 'parent_title': '', 'start_page': 8, 'end_page': 8, 'file': 'Книга_4.json', 'basin': 'Печора', 'chunk_index': 1, 'total_chunks': 1, 'order': 1}, page_content='Введение В книге 4 «Схемы комплексного использования и охраны водных объектов, включая Ндв, бассейна реки Печоры» (далее Схема) представлены расчеты водохозяйственных балансов и балансов загрязняющих веществ, выполненные по расчетным и водохозяйственным участкам для лет различной водности (50 , 75  и 95  обеспеченности). Кроме того, в книге приведены расчеты величин пре  дельного изъятия воды из поверхностных водных объектов, которые были исполь  зованы в расчетах водохозяйственных балансов. Представленные материалы служат обоснованием необходимости выпол  нения водохозяйственных и водоохранных мероприятий для решения проблем водохозяйственного комплекса. 1. Водохозяйственные Балансы 1.1. Методика расчета водохозяйственных балансов В качестве методической основы расчета водохоз

In [20]:
# Путь для сохранения файлов
output_folder = "processed_output"
os.makedirs(output_folder, exist_ok=True)

# Запись в JSON
json_output_path = os.path.join(output_folder, "processed_documents.json")
with open(json_output_path, "w", encoding="utf-8") as json_file:
    json.dump(
        [
            {"metadata": doc.metadata, "page_content": doc.page_content}
            for doc in processed_documents
        ],
        json_file,
        ensure_ascii=False,
        indent=4
    )

# Запись метаданных в CSV
metadata_csv_path = os.path.join(output_folder, "metadata.csv")
metadata_df = pd.DataFrame([doc.metadata for doc in processed_documents])
metadata_df.to_csv(metadata_csv_path, index=False, encoding="utf-8")

# Запись каждого документа в отдельный текстовый файл
for idx, doc in enumerate(processed_documents, start=1):
    text_file_path = os.path.join(output_folder, f"document_{idx}.txt")
    with open(text_file_path, "w", encoding="utf-8") as text_file:
        text_file.write(doc.page_content)

print(f"Данные сохранены:\n- JSON: {json_output_path}\n- CSV: {metadata_csv_path}\n- Текстовые файлы в папке: {output_folder}")

Данные сохранены:
- JSON: processed_output/processed_documents.json
- CSV: processed_output/metadata.csv
- Текстовые файлы в папке: processed_output


In [21]:
import json
import os

# Путь для сохранения файла
output_folder = "processed_output"
os.makedirs(output_folder, exist_ok=True)
output_file_path = os.path.join(output_folder, "all_documents.json")

# Подготовка данных для записи
data_to_save = [
    {
        "metadata": doc.metadata,
        "page_content": doc.page_content
    }
    for doc in processed_documents
]

# Запись в JSON
with open(output_file_path, "w", encoding="utf-8") as json_file:
    json.dump(data_to_save, json_file, ensure_ascii=False, indent=4)

print(f"Все данные успешно сохранены в один файл: {output_file_path}")

Все данные успешно сохранены в один файл: processed_output/all_documents.json


In [22]:
import json
from langchain_core.documents import Document

# Путь к JSON-файлу
input_file_path = "processed_output/all_documents.json"

# Чтение данных из JSON
with open(input_file_path, "r", encoding="utf-8") as json_file:
    data = json.load(json_file)

# Восстановление массива объектов Document
restored_documents = [
    Document(metadata=item["metadata"], page_content=item["page_content"])
    for item in data
]

print(f"Загружено {len(restored_documents)} документов.")

Загружено 2328 документов.


In [23]:
restored_documents

[Document(metadata={'title': 'ВВЕДЕНИЕ', 'level': 1, 'parent_title': '', 'start_page': 8, 'end_page': 8, 'file': 'Книга_4.json', 'basin': 'Печора', 'chunk_index': 1, 'total_chunks': 1, 'order': 1}, page_content='Введение В книге 4 «Схемы комплексного использования и охраны водных объектов, включая Ндв, бассейна реки Печоры» (далее Схема) представлены расчеты водохозяйственных балансов и балансов загрязняющих веществ, выполненные по расчетным и водохозяйственным участкам для лет различной водности (50 , 75  и 95  обеспеченности). Кроме того, в книге приведены расчеты величин пре  дельного изъятия воды из поверхностных водных объектов, которые были исполь  зованы в расчетах водохозяйственных балансов. Представленные материалы служат обоснованием необходимости выпол  нения водохозяйственных и водоохранных мероприятий для решения проблем водохозяйственного комплекса. 1. Водохозяйственные Балансы 1.1. Методика расчета водохозяйственных балансов В качестве методической основы расчета водохоз